In [1]:
import sys
sys.path.append('../src/')
import time
import os
import copy

import numpy as np
import tensorly as tn
import matlab.engine

from loewnerize_acts import loewnerize_acts
import ll1_tools

## Load raw data for LenetLinear classifier model

In [2]:
targets_path = '../data/LenetLinear/activations/test/targets.npy'
targets = np.load(targets_path)

inputs_path = '../data/LenetLinear/activations/test/99/layers.layer_0.linear.npy'
inputs_raw = np.load(inputs_path)
print('Inputs shape')
print(inputs_raw.shape)

outputs_path = '../data/LenetLinear/activations/test/99/layers.layer_0.rat.npy'
outputs_raw = np.load(outputs_path)
print('Outputs shape')
print(outputs_raw.shape)
print(outputs_raw[0,0,0])

tensorlab_path = '~/ware/matlab_tools/tensorlab'
# tensorlab_path = '~/tools/matlab_tools/Tensorlab'

Inputs shape
(39, 256, 10)
Outputs shape
(39, 256, 10)
-5.9573436


In [3]:
lwn_tensors = loewnerize_acts(inputs_raw, outputs_raw, targets, tensorlab_path)
# datapath = '../data/LenetLinear/activations/test/99/loewnerized_acts'
# np.savez(datapath, *lwn_tensors)

In [4]:
for lwn_trgt in lwn_tensors:
    print(lwn_trgt.shape)
    print(type(lwn_trgt))

(5, 5, 979)
<class 'numpy.ndarray'>
(5, 5, 1133)
<class 'numpy.ndarray'>
(5, 5, 1030)
<class 'numpy.ndarray'>
(5, 5, 1008)
<class 'numpy.ndarray'>
(5, 5, 980)
<class 'numpy.ndarray'>
(5, 5, 890)
<class 'numpy.ndarray'>
(5, 5, 956)
<class 'numpy.ndarray'>
(5, 5, 1027)
<class 'numpy.ndarray'>
(5, 5, 973)
<class 'numpy.ndarray'>
(5, 5, 1008)
<class 'numpy.ndarray'>


## perform (L,L,1) decomposition - per target (0-9)

In [5]:
eng = matlab.engine.start_matlab()
s = eng.genpath(tensorlab_path)
eng.addpath(s, nargout=0)

num_terms = 20
rat_deg = 3

L = rat_deg * np.ones(num_terms)
Us = list()
outs = list()

tic = time.perf_counter()
for tns in lwn_tensors:
    tmp_U, tmp_out = eng.ll1(tns, L, nargout=2)
    Us.append(tmp_U)
    outs.append(tmp_out)
toc = time.perf_counter()
print(toc-tic)

> In ll1_core/state (line 238)
In ll1_core (line 191)
In ll1_nls (line 40)
In ll1 (line 551)

> In ll1_core/state (line 238)
In ll1_core/grad (line 256)
In nls_gndl (line 369)
In ll1_core (line 193)
In ll1_nls (line 40)
In ll1 (line 551)

> In ll1_core/state (line 238)
In ll1_core/grad (line 256)
In nls_gndl (line 369)
In ll1_core (line 193)
In ll1_nls (line 40)
In ll1 (line 551)

> In ll1_core/state (line 238)
In ll1_core/grad (line 256)
In nls_gndl (line 369)
In ll1_core (line 193)
In ll1_nls (line 40)
In ll1 (line 551)

> In ll1_core/state (line 238)
In ll1_core/grad (line 256)
In nls_gndl (line 369)
In ll1_core (line 193)
In ll1_nls (line 40)
In ll1 (line 551)

> In ll1_core/state (line 238)
In ll1_core/grad (line 256)
In nls_gndl (line 369)
In ll1_core (line 193)
In ll1_nls (line 40)
In ll1 (line 551)

> In ll1_core/state (line 238)
In ll1_core/grad (line 256)
In nls_gndl (line 369)
In ll1_core (line 193)
In ll1_nls (line 40)
In ll1 (line 551)

> In ll1_core/state (line 238)
In ll

Operation terminated by user during nls_gndl/PC


In mpcg (line 86)
        else y = M(r); end

In nls_gndl (line 376)
                mpcg(@JHJx,-grad,options.CGTol,options.CGMaxIter,dF.PC, ...

In ll1_core (line 193)
    [U,output] = options.Algorithm(@objfun,dF,U0(:).',options);

In ll1_nls (line 40)
        [U, output] = ll1_core(T,U0,'Algorithm',@nls_gndl,'OptimizationType', ...

In ll1 (line 667)
    [U,output.Refinement] = options.Refinement(Tunc,UA0, ...



TypeError: cannot unpack non-iterable NoneType object

## perform (L,L,1) decomposition - entire collection

In [13]:
super_lwn = lwn_tensors[0]
print(type(super_lwn))
for i in range(9):
    super_lwn = np.dstack((super_lwn, lwn_tensors[i+1]))

# shuffle
np.random.shuffle(super_lwn)
print(super_lwn.shape)

super_lwn_1 = super_lwn[:,:,:(9984//2)]
super_lwn_2 = super_lwn[:,:,(9984//2):]

print(super_lwn_1.shape)
print(super_lwn_2.shape)


<class 'numpy.ndarray'>
(5, 5, 9984)
(5, 5, 4992)
(5, 5, 4992)


In [14]:
num_terms = 25
rat_deg = 3
L = rat_deg * np.ones(num_terms)

tic = time.perf_counter()
all_U_1, all_out_1 = eng.ll1(super_lwn_1, L, nargout=2)
all_U_2, all_out_2 = eng.ll1(super_lwn_2, L, nargout=2)

toc = time.perf_counter()
print(toc-tic)

ValueError: ndarray is not contiguous

In [26]:
res = 1 - eng.frobll1res(super_lwn,all_U) / eng.frob(super_lwn)
print(f"Residual: {res}")

Residual: 0.9999975467553421


<class 'matlab.double'>
5
[[[-0.08744425926045718,-0.020078094975592098,0.1506763323233622,-0.02343672915459294,0.3978458481952205,-0.09652855883128453,-0.14900408741020787,0.03191690243727363,-0.46394259273275784,0.42426905707255336,-0.06826391578555047,-0.05784724479067682,-0.4529365989170042,0.12812337590466782,-0.09619260277702257,0.05620594233859544,-0.16677780099314177,0.9945726677678062,0.0794497355281989,-0.024754087772444144,0.6814414803844278,-0.5885995401990894,-0.06988957638977267,-0.2556992731597567,-1.020248767380917,0.6817675268914829,0.32065233921274583,-0.6781214551738919,-0.029353517893802028,0.37048692289407525,-0.12401289889528178,-0.21698282664421153,-0.2093345407434397,-0.1626124631460084,0.020379718864016017,0.10343161347897989,0.06428786913941043,-0.2510235617728851,0.08777100896110523,0.04740377684665553,0.42680504925417195,0.568486197204304,0.03442457941389643,-0.11732209395358462,0.011137918221308496,-0.2658231218120344,0.00204204663861951,-0.3926449701547705